***Geospatial Data Science Handbook***
- Author: Dr. Isam Al Jawarneh
- Copyright (c) [2024] [Isam Al Jawarneh]

https://towardsdatascience.com/data-101s-spatial-visualizations-and-analysis-in-python-with-folium-39730da2adf

https://github.com/justinm0rgan/citibike-heatmap

#Prepare: Install the needed packages

In [ ]:
# Install Folium library for creating interactive maps
!pip install folium
# Install uszipcode library for accessing US ZIP Code data
!pip install uszipcode
# Install pygeohash library for encoding and decoding geographical coordinates into geohashes
%pip install pygeohash
# Install Geopandas library for working with geospatial data
!pip install geopandas


# Mount the drive

Mount the drive so that you can read the data from google drive

---



In [ ]:
from google.colab import drive
drive.mount('/content/drive')

KeyboardInterrupt: 

# Import the Libraries

In [7]:
from pandas import Series, DataFrame # Import Series and DataFrame classes from pandas library
import pandas as pd # Import pandas library with alias pd
import numpy as np # Import numpy library with alias np
import plotly.graph_objs as go # Import graph objects module from plotly library with alias go
from IPython.display import Image # Import Image class from IPython.display module
import folium # Import folium library for creating interactive maps
from folium import IFrame # Import IFrame class from folium library
from folium.plugins import MarkerCluster # Import MarkerCluster plugin from folium.plugins module
from folium import plugins # Import plugins module from folium library
from datetime import datetime # Import datetime class from datetime module
import datetime as dt # Import datetime module with alias dt
import json # Import json module for working with JSON data
from scipy import stats # Import stats module from scipy library
import os # Import os module for interacting with the operating system
import matplotlib.pyplot as plt
import seaborn as sns

# CONFIG: Sampling Parameters

In [ ]:
sampling_fraction = 0.6
geohash_precision = 6

# Loading Data & Analysis: Mobility Data

In [ ]:
# Read the CSV file into a pandas DataFrame named "trips"
trips = pd.read_csv("/content/drive/MyDrive/Found. of DS Project/nyc_mobility/nyc1.csv")


In [ ]:
#directoryPath = "/content/drive/MyDrive/Papers/dimensionality_reduction/datasets/NYC/trips/"

In [ ]:
#Merge Multiple CSV Files in Python

In [ ]:
'''file_path_1 ='/content/drive/MyDrive/Papers/dimensionality_reduction/datasets/NYC/pollution/NYC_Pilot1_PM.csv'
file_path_2 = "/content/drive/MyDrive/Papers/dimensionality_reduction/datasets/NYC/pollution/NYC_Pilot2_PM_Part1.csv"
file_path_3 = "/content/drive/MyDrive/Papers/dimensionality_reduction/datasets/NYC/pollution/NYC_Pilot2_PM_Part2.csv"
file_path_4 = "/content/drive/MyDrive/Papers/dimensionality_reduction/datasets/NYC/pollution/NYC_Pilot2_PM_Part3.csv"'''

'file_path_1 =\'/content/drive/MyDrive/Papers/dimensionality_reduction/datasets/NYC/pollution/NYC_Pilot1_PM.csv\'\nfile_path_2 = "/content/drive/MyDrive/Papers/dimensionality_reduction/datasets/NYC/pollution/NYC_Pilot2_PM_Part1.csv"\nfile_path_3 = "/content/drive/MyDrive/Papers/dimensionality_reduction/datasets/NYC/pollution/NYC_Pilot2_PM_Part2.csv"\nfile_path_4 = "/content/drive/MyDrive/Papers/dimensionality_reduction/datasets/NYC/pollution/NYC_Pilot2_PM_Part3.csv"'

In [ ]:
'''import pandas as pd
files = [file_path_1, file_path_2,file_path_3,file_path_4]
trips = pd.DataFrame()
for file in files:
    data = pd.read_csv(file)
    trips = pd.concat([trips, data], axis=0)
#df.to_csv('nyc_pollution.csv', index=False)'''

"import pandas as pd\nfiles = [file_path_1, file_path_2,file_path_3,file_path_4]\ntrips = pd.DataFrame()\nfor file in files:\n    data = pd.read_csv(file)\n    trips = pd.concat([trips, data], axis=0)\n#df.to_csv('nyc_pollution.csv', index=False)"

In [ ]:
# Return the type of the dataframe trips
type(trips)

pandas.core.frame.DataFrame

In [ ]:
# Retrive the number of rows and number of columns in the dataframe trip
trips.shape

(1445285, 22)

In [ ]:
# Retrieve the first 2 rows of the DataFrame trips to inspect its structure and content
trips.head(2)

id  VendorID lpep_pickup_datetime Lpep_dropoff_datetime Store_and_fwd_flag  \
0   0         2  2016-01-01 00:29:24   2016-01-01 00:39:36                  N   
1   1         2  2016-01-01 00:19:39   2016-01-01 00:39:18                  N   

   RateCodeID  Pickup_longitude  Pickup_latitude  Dropoff_longitude  \
0           1        -73.928642        40.680611         -73.924278   
1           1        -73.952675        40.723175         -73.923920   

   Dropoff_latitude  ...  Fare_amount  Extra  MTA_tax  Tip_amount  \
0         40.698044  ...          8.0    0.5      0.5        1.86   
1         40.761379  ...         15.5    0.5      0.5        0.00   

   Tolls_amount  Ehail_fee  improvement_surcharge  Total_amount  Payment_type  \
0           0.0        NaN                    0.3         11.16             1   
1           0.0        NaN                    0.3         16.80             2   

   Trip_type  
0        1.0  
1        1.0  

[2 rows x 22 columns]

In [ ]:
'''import glob
import pandas as pd

trips = pd.DataFrame()
for file_name in glob.glob(directoryPath+'*.csv'):
    x = pd.read_csv(file_name, low_memory=False)
    trips = pd.concat([trips,x],axis=0)'''
    #this is for multiple files

"import glob\nimport pandas as pd\n\ntrips = pd.DataFrame()\nfor file_name in glob.glob(directoryPath+'*.csv'):\n    x = pd.read_csv(file_name, low_memory=False)\n    trips = pd.concat([trips,x],axis=0)"

In [ ]:
# Retrieve the number of columns in the DataFrame trips
columns=trips.shape[1]
print(columns)

# Retrieve the number of rows in the DataFrame trips
rows=trips.shape[0]
print(rows)

22
1445285


Convert datetime object column to datetime series

In [ ]:
'''trips['time'] = pd.to_datetime(\
                trips['time'],dayfirst = True)
trips['time'] = pd.to_datetime(\
                trips['time'],dayfirst = True)'''


"trips['time'] = pd.to_datetime(                trips['time'],dayfirst = True)\ntrips['time'] = pd.to_datetime(                trips['time'],dayfirst = True)"

add columns month, time, day

# Remove erroneous coordinates (0,0) from the dataset - Mobility Data


In [ ]:
# Rename the 'Pickup_longitude' column to 'longitude'
# Rename 'Pickup_latitude' column to 'latitude' in the DataFrame trips
# The 'inplace=True' parameter ensures that the changes are applied to the DataFrame itself
trips.rename(columns={'Pickup_longitude':'longitude', 'Pickup_latitude':'latitude'}, inplace=True)

In [ ]:
# Filter the DataFrame trips to remove rows where the latitude is 0 and longitude is 0
trips = trips[(trips['latitude'] != 0 ) & (trips['longitude']!=0 )]

### Check the size before and after the filter

In [ ]:
#Before the filter
print("Before filtering:", rows)

#After the filter
rows2=trips.shape[0]
print("After filtering: ", rows2)

Before filtering: 1445285
After filtering:  1442776


# Geohash - Mobility Data

### Import the libraries

In [ ]:
!pip install pygeohash

In [ ]:
import pygeohash as gh  # Import pygeohash library with alias gh for encoding and decoding geographic coordinates into geohashes
import geopandas as gpd  # Import the geopandas library with alias gpd for working with geospatial data

### Generate geohash for each tuple (long, lat)

In [ ]:
# Measure the execution time of the code within this cell
%%time

# Encode latitude and longitude coordinates into geohashes and assign them to a new column 'geohash' in the DataFrame trips
# The lambda function applies the encoding operation to each row of the DataFrame using the specified geohash precision
trips['geohash'] = trips.apply(lambda x: gh.encode(x.latitude, x.longitude, precision=geohash_precision), axis=1)


CPU times: user 53.8 s, sys: 1.39 s, total: 55.1 s
Wall time: 1min 2s


In [ ]:
# Measure the average execution time of the trips.head(2) operation
%timeit trips.head(2)

24.8 µs ± 4.13 µs per loop (mean ± std. dev. of 7 runs, 10000 loops each)


In [ ]:
# Display number of rows
trips.shape[0]

1442776

In [ ]:
# Display the first 2 rows
trips.head(2)

id  VendorID lpep_pickup_datetime Lpep_dropoff_datetime Store_and_fwd_flag  \
0   0         2  2016-01-01 00:29:24   2016-01-01 00:39:36                  N   
1   1         2  2016-01-01 00:19:39   2016-01-01 00:39:18                  N   

   RateCodeID  longitude   latitude  Dropoff_longitude  Dropoff_latitude  ...  \
0           1 -73.928642  40.680611         -73.924278         40.698044  ...   
1           1 -73.952675  40.723175         -73.923920         40.761379  ...   

   Extra  MTA_tax  Tip_amount  Tolls_amount  Ehail_fee  improvement_surcharge  \
0    0.5      0.5        1.86           0.0        NaN                    0.3   
1    0.5      0.5        0.00           0.0        NaN                    0.3   

   Total_amount  Payment_type  Trip_type  geohash  
0         11.16             1        1.0   dr5rmt  
1         16.80             2        1.0   dr5rtj  

[2 rows x 23 columns]

### Convert trips to GeoPandas

In [ ]:
# Return the type of the dataframe trip
type(trips)

pandas.core.frame.DataFrame

In [ ]:
# Convert to Geopandas Geodataframe
%%time

# Create a GeoDataFrame gdf_trips from the DataFrame trips, specifying the geometry column using longitude and latitude coordinates
gdf_trips = gpd.GeoDataFrame(trips, geometry=gpd.points_from_xy(trips.longitude, trips.latitude))

CPU times: user 6.28 s, sys: 337 ms, total: 6.62 s
Wall time: 6.77 s


In [ ]:
# Determine the type of object represented by the variable gdf_trips
type(gdf_trips)

geopandas.geodataframe.GeoDataFrame

In [ ]:
# Print the Coordinate Reference System (CRS) of the GeoDataFrame gdf_trips
print(gdf_trips.crs)

None


In [ ]:
# RUN the cell before
# Sample a fraction of the GeoDataFrame gdf_trips
# The sampling fraction determines the proportion of rows to be randomly sampled from the GeoDataFrame

gdf_trips=gdf_trips.sample(frac=sampling_fraction) # sampling_fraction = 0.6

In [ ]:
# Print the Coordinate Reference System (CRS) of the GeoDataFrame gdf_trips - after the sampling (it should stay the same)
print(gdf_trips.crs)

None


In [ ]:
# The CRS for trips should remain geographic 4326
gdf_trips = gdf_trips.set_crs('epsg:4326')
print(gdf_trips)

              id  VendorID lpep_pickup_datetime Lpep_dropoff_datetime  \
1000690  1000690         1  2016-01-22 00:38:32   2016-01-22 00:43:04   
990579    990579         1  2016-01-21 20:27:14   2016-01-21 20:49:51   
371152    371152         2  2016-01-08 22:16:13   2016-01-08 22:18:31   
1260670  1260670         2  2016-01-28 20:21:32   2016-01-28 20:26:04   
540455    540455         2  2016-01-12 12:30:25   2016-01-12 12:42:40   
...          ...       ...                  ...                   ...   
426497    426497         2  2016-01-09 21:46:38   2016-01-09 22:05:58   
358824    358824         2  2016-01-08 18:42:32   2016-01-08 18:55:33   
101317    101317         1  2016-01-02 20:38:35   2016-01-02 20:41:49   
589484    589484         2  2016-01-13 15:56:33   2016-01-13 15:57:11   
594322    594322         2  2016-01-13 17:36:47   2016-01-13 17:45:53   

        Store_and_fwd_flag  RateCodeID  longitude   latitude  \
1000690                  N           1 -73.957458  40.71806

In [ ]:
# Display the shape of the GeoDataFrame gdf_trips
gdf_trips.shape

(865666, 24)

In [ ]:
# Display the first 2 rows of the GeoDataFrame gdf_trips
gdf_trips.head(2)

id  VendorID lpep_pickup_datetime Lpep_dropoff_datetime  \
1000690  1000690         1  2016-01-22 00:38:32   2016-01-22 00:43:04   
990579    990579         1  2016-01-21 20:27:14   2016-01-21 20:49:51   

        Store_and_fwd_flag  RateCodeID  longitude   latitude  \
1000690                  N           1 -73.957458  40.718060   
990579                   N           1 -73.859329  40.668201   

         Dropoff_longitude  Dropoff_latitude  ...  MTA_tax  Tip_amount  \
1000690         -73.957863         40.731804  ...      0.5        1.35   
990579          -73.695679         40.697994  ...      0.5        0.00   

         Tolls_amount  Ehail_fee  improvement_surcharge  Total_amount  \
1000690           0.0        NaN                    0.3          8.15   
990579            0.0        NaN                    0.3         35.30   

         Payment_type  Trip_type  geohash                    geometry  
1000690             1        1.0   dr5rth  POINT (-73.95746 40.71806)  
990579              2        1.0   dr5rr7  POINT (-73.85933 40.66820)  

[2 rows x 24 columns]

it additionally trips now has the geometry column

### Convert polygons to GeoPandas

In [ ]:
# BASELINE: original Neighbourhoods

# Define the file path to the GeoJSON file containing NYC neighborhood polygons
geojson_file = "/content/drive/MyDrive/Found. of DS Project/nyc_polygon.geojson"

# Read the GeoJSON file and create a GeoDataFrame named neighborhoods_original
neighborhoods_original = gpd.read_file(geojson_file)

In [ ]:
# Display the shape of the GeoDataFrame neighborhoods_original (rows, columns)
neighborhoods_original.shape

(310, 5)

In [ ]:
# Display the first 2 rows of the GeoDataFrame neighborhoods_original
neighborhoods_original.head(2)

neighborhood boroughCode borough  \
0         Allerton           2   Bronx   
1  Alley Pond Park           4  Queens   

                                                 @id  \
0  http://nyc.pediacities.com/Resource/Neighborho...   
1  http://nyc.pediacities.com/Resource/Neighborho...   

                                            geometry  
0  POLYGON ((-73.84860 40.87167, -73.84582 40.870...  
1  POLYGON ((-73.74333 40.73888, -73.74371 40.739...

In [ ]:
# Display the first 2 rows of the GeoDataFrame gdf_trips
gdf_trips.head(2)

id  VendorID lpep_pickup_datetime Lpep_dropoff_datetime  \
1000690  1000690         1  2016-01-22 00:38:32   2016-01-22 00:43:04   
990579    990579         1  2016-01-21 20:27:14   2016-01-21 20:49:51   

        Store_and_fwd_flag  RateCodeID  longitude   latitude  \
1000690                  N           1 -73.957458  40.718060   
990579                   N           1 -73.859329  40.668201   

         Dropoff_longitude  Dropoff_latitude  ...  MTA_tax  Tip_amount  \
1000690         -73.957863         40.731804  ...      0.5        1.35   
990579          -73.695679         40.697994  ...      0.5        0.00   

         Tolls_amount  Ehail_fee  improvement_surcharge  Total_amount  \
1000690           0.0        NaN                    0.3          8.15   
990579            0.0        NaN                    0.3         35.30   

         Payment_type  Trip_type  geohash                    geometry  
1000690             1        1.0   dr5rth  POINT (-73.95746 40.71806)  
990579              2        1.0   dr5rr7  POINT (-73.85933 40.66820)  

[2 rows x 24 columns]

### Spatial Analysis and Join Operations with GeoDataFrames
Keeping geometry column from both dataframes when applying sjoin() using GeoPandas
this is so because later on we group by NAME(district in Shenzhen)
also, the CRS (coordinate reference system) is 3857 in this case which is a projected CRS not geographic CRS, to calculate the distance corercctly between centroids
https://gis.stackexchange.com/questions/393387/keeping-geometry-column-from-both-dataframes-when-applying-sjoin-using-geopand

In [ ]:
# Convert the geometry column to EPSG:3857 CRS for accurate spatial analysis.
neighborhoods_original['geometryn'] = neighborhoods_original.geometry.to_crs("epsg:3857")

In [ ]:
# Retrieve the coordinate reference system (CRS) information from the GeoDataFrame gdf_trips
gdf_trips.crs

<Geographic 2D CRS: EPSG:4326>
Name: WGS 84
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
Area of Use:
- name: World.
- bounds: (-180.0, -90.0, 180.0, 90.0)
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [ ]:
# Retrieve the coordinate reference system (CRS) information from the GeoDataFrame neighborhoods_original
neighborhoods_original.crs

<Geographic 2D CRS: EPSG:4326>
Name: WGS 84
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
Area of Use:
- name: World.
- bounds: (-180.0, -90.0, 180.0, 90.0)
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [ ]:
# Retrieve the coordinate reference system (CRS) information from the 'geometryn' column of the GeoDataFrame neighborhoods_original
neighborhoods_original.geometryn.crs

<Projected CRS: EPSG:3857>
Name: WGS 84 / Pseudo-Mercator
Axis Info [cartesian]:
- X[east]: Easting (metre)
- Y[north]: Northing (metre)
Area of Use:
- name: World between 85.06°S and 85.06°N.
- bounds: (-180.0, -85.06, 180.0, 85.06)
Coordinate Operation:
- name: Popular Visualisation Pseudo-Mercator
- method: Popular Visualisation Pseudo Mercator
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [ ]:
%%time
# Perform a spatial join between gdf_trips and neighborhoods_original, considering trips that are within neighborhood polygons.

#BASELINE
# we join by sjoin, but we have geohash so, we sample stratified by geohash
# so, we join only to get the metrics but the stratified sampling is based on the fine-grained division (geohash in this case)

# Store the result of the spatial join in the variable sjoined_trips_original.
sjoined_trips_original = gpd.sjoin(gdf_trips, neighborhoods_original, predicate="within")

CPU times: user 8.62 s, sys: 823 ms, total: 9.45 s
Wall time: 13.8 s


In [ ]:
# Display the first 2 rows of the resulting GeoDataFrame.
sjoined_trips_original.head(2)

id  VendorID lpep_pickup_datetime Lpep_dropoff_datetime  \
1000690  1000690         1  2016-01-22 00:38:32   2016-01-22 00:43:04   
1260670  1260670         2  2016-01-28 20:21:32   2016-01-28 20:26:04   

        Store_and_fwd_flag  RateCodeID  longitude   latitude  \
1000690                  N           1 -73.957458  40.718060   
1260670                  N           1 -73.957527  40.718025   

         Dropoff_longitude  Dropoff_latitude  ...  Payment_type  Trip_type  \
1000690         -73.957863         40.731804  ...             1        1.0   
1260670         -73.953514         40.728065  ...             2        1.0   

         geohash                    geometry  index_right  neighborhood  \
1000690   dr5rth  POINT (-73.95746 40.71806)          303  Williamsburg   
1260670   dr5rth  POINT (-73.95753 40.71803)          303  Williamsburg   

         boroughCode   borough  \
1000690            4  Brooklyn   
1260670            4  Brooklyn   

                                                       @id  \
1000690  http://nyc.pediacities.com/Resource/Neighborho...   
1260670  http://nyc.pediacities.com/Resource/Neighborho...   

                                                 geometryn  
1000690  POLYGON ((-8232919.255 4971877.704, -8232410.0...  
1260670  POLYGON ((-8232919.255 4971877.704, -8232410.0...  

[2 rows x 30 columns]

In [ ]:
# Retrieve the type of the variable sjoined_trips_original, indicating the data type of the object it refers to.
type(sjoined_trips_original)

geopandas.geodataframe.GeoDataFrame

In [ ]:
# Counting unique values
n = len(pd.unique(sjoined_trips_original['neighborhood']))
print("No.of.unique name values :", n)

No.of.unique name values : 215


In [ ]:
# Retrieve the shape of the sjoined_trips_original GeoDataFrame, which indicates the number of rows and columns in the dataset.
sjoined_trips_original.shape

(864936, 30)

In [ ]:
# Retrieve the data types of columns in the sjoined_trips_original GeoDataFrame, indicating the data type of each attribute or column.
sjoined_trips_original.dtypes

id                          int64
VendorID                    int64
lpep_pickup_datetime       object
Lpep_dropoff_datetime      object
Store_and_fwd_flag         object
RateCodeID                  int64
longitude                 float64
latitude                  float64
Dropoff_longitude         float64
Dropoff_latitude          float64
Passenger_count             int64
Trip_distance             float64
Fare_amount               float64
Extra                     float64
MTA_tax                   float64
Tip_amount                float64
Tolls_amount              float64
Ehail_fee                 float64
improvement_surcharge     float64
Total_amount              float64
Payment_type                int64
Trip_type                 float64
geohash                    object
geometry                 geometry
index_right                 int64
neighborhood               object
boroughCode                object
borough                    object
@id                        object
geometryn     

# SAMPLING AND MAP GENERATION

### SAMPLING - PERFORMANCE

###  Sampling by Geohash with Variable Sampling Fraction

In [ ]:
%%time
# Sampling by geohash change fraction sampling rate
# Group the spatially joined data 'sjoined_trips_original' by neighborhood
# Then within each neighborhood group, sample a fraction of the data based on the specified 'sampling_fraction'.

sampled_geohash_data_base= sjoined_trips_original.groupby('neighborhood').apply(lambda x: x.sample(frac=sampling_fraction)) #sampling_fraction = 0.6
# The resulting sampled data is stored in the 'sampled_geohash_data_base' variable.

CPU times: user 3.75 s, sys: 200 ms, total: 3.95 s
Wall time: 4.01 s


In [ ]:
# Retrieve the shape of the sampled_geohash_data_base DataFrame, indicating the number of rows and columns in the dataset.
sampled_geohash_data_base.shape

(518967, 30)

In [ ]:
# Print the first two rows
sampled_geohash_data_base.head(2)

id  VendorID lpep_pickup_datetime  \
neighborhood                                                   
Allerton     1067173  1067173         2  2016-01-23 13:27:25   
             874092    874092         2  2016-01-19 10:22:21   

                     Lpep_dropoff_datetime Store_and_fwd_flag  RateCodeID  \
neighborhood                                                                
Allerton     1067173   2016-01-23 13:49:53                  N           1   
             874092    2016-01-19 11:01:27                  N           1   

                      longitude   latitude  Dropoff_longitude  \
neighborhood                                                    
Allerton     1067173 -73.866951  40.865322         -73.861137   
             874092  -73.867523  40.864315         -73.928116   

                      Dropoff_latitude  ...  Payment_type  Trip_type  geohash  \
neighborhood                            ...                                     
Allerton     1067173         40.813419  ...             1        1.0   dr72rp   
             874092          40.743519  ...             2        1.0   dr72rp   

                                        geometry  index_right  neighborhood  \
neighborhood                                                                  
Allerton     1067173  POINT (-73.86695 40.86532)            0      Allerton   
             874092   POINT (-73.86752 40.86432)            0      Allerton   

                      boroughCode  borough  \
neighborhood                                 
Allerton     1067173            2    Bronx   
             874092             2    Bronx   

                                                                    @id  \
neighborhood                                                              
Allerton     1067173  http://nyc.pediacities.com/Resource/Neighborho...   
             874092   http://nyc.pediacities.com/Resource/Neighborho...   

                                                              geometryn  
neighborhood                                                             
Allerton     1067173  POLYGON ((-8220788.214 4993431.406, -8220479.3...  
             874092   POLYGON ((-8220788.214 4993431.406, -8220479.3...  

[2 rows x 30 columns]

In [ ]:
# Print the column names of the sampled_geohash_data_base DataFrame, showing the attributes present in the dataset.
print(sampled_geohash_data_base.columns)

Index(['id', 'VendorID', 'lpep_pickup_datetime', 'Lpep_dropoff_datetime',
       'Store_and_fwd_flag', 'RateCodeID', 'longitude', 'latitude',
       'Dropoff_longitude', 'Dropoff_latitude', 'Passenger_count',
       'Trip_distance', 'Fare_amount', 'Extra', 'MTA_tax', 'Tip_amount',
       'Tolls_amount', 'Ehail_fee', 'improvement_surcharge', 'Total_amount',
       'Payment_type', 'Trip_type', 'geohash', 'geometry', 'index_right',
       'neighborhood', 'boroughCode', 'borough', '@id', 'geometryn'],
      dtype='object')


In [ ]:
#take only readings greater than specific threshold to count reading in each polygon greater than that threshold
#sampled_geohash_data_base = sampled_geohash_data_base[sampled_geohash_data_base.pm25>= 3 ]

In [ ]:
# counting unique values
n = len(pd.unique(sampled_geohash_data_base['neighborhood']))
print("No.of.unique name values :", n)

No.of.unique name values : 215


### Sampling Entire Fractions of Grouped Data by Neighborhood

In [ ]:
%%time
# Original

# Group the spatially joined data 'sjoined_trips_original' by neighborhood, then within each neighborhood group, sample the entire fraction of the data (frac=1).
sampled_geohash_data_original = sjoined_trips_original.groupby('neighborhood').apply(lambda x: x.sample(frac=1))
# The resulting sampled data is stored in the 'sampled_geohash_data_original' variable

CPU times: user 4.04 s, sys: 370 ms, total: 4.41 s
Wall time: 4.44 s


In [ ]:
# Retrieve the shape of the sampled_geohash_data_base DataFrame, indicating the number of rows and columns in the dataset.
sampled_geohash_data_original.shape

(864936, 30)

In [ ]:
# Print the first two rows
sampled_geohash_data_original.head(2)

id  VendorID lpep_pickup_datetime  \
neighborhood                                                   
Allerton     1147249  1147249         2  2016-01-26 12:37:38   
             876331    876331         2  2016-01-19 11:51:19   

                     Lpep_dropoff_datetime Store_and_fwd_flag  RateCodeID  \
neighborhood                                                                
Allerton     1147249   2016-01-26 12:52:34                  N           1   
             876331    2016-01-19 11:55:13                  N           1   

                      longitude   latitude  Dropoff_longitude  \
neighborhood                                                    
Allerton     1147249 -73.848511  40.871597         -73.881035   
             876331  -73.856529  40.857964         -73.859520   

                      Dropoff_latitude  ...  Payment_type  Trip_type  geohash  \
neighborhood                            ...                                     
Allerton     1147249         40.880032  ...             2        1.0   dr72x8   
             876331          40.867062  ...             2        1.0   dr72rm   

                                        geometry  index_right  neighborhood  \
neighborhood                                                                  
Allerton     1147249  POINT (-73.84851 40.87160)            0      Allerton   
             876331   POINT (-73.85653 40.85796)            0      Allerton   

                      boroughCode  borough  \
neighborhood                                 
Allerton     1147249            2    Bronx   
             876331             2    Bronx   

                                                                    @id  \
neighborhood                                                              
Allerton     1147249  http://nyc.pediacities.com/Resource/Neighborho...   
             876331   http://nyc.pediacities.com/Resource/Neighborho...   

                                                              geometryn  
neighborhood                                                             
Allerton     1147249  POLYGON ((-8220788.214 4993431.406, -8220479.3...  
             876331   POLYGON ((-8220788.214 4993431.406, -8220479.3...  

[2 rows x 30 columns]

In [ ]:
# Print the column names of the sampled_geohash_data_original DataFrame, showing the attributes present in the dataset.
print(sampled_geohash_data_original.columns)

Index(['id', 'VendorID', 'lpep_pickup_datetime', 'Lpep_dropoff_datetime',
       'Store_and_fwd_flag', 'RateCodeID', 'longitude', 'latitude',
       'Dropoff_longitude', 'Dropoff_latitude', 'Passenger_count',
       'Trip_distance', 'Fare_amount', 'Extra', 'MTA_tax', 'Tip_amount',
       'Tolls_amount', 'Ehail_fee', 'improvement_surcharge', 'Total_amount',
       'Payment_type', 'Trip_type', 'geohash', 'geometry', 'index_right',
       'neighborhood', 'boroughCode', 'borough', '@id', 'geometryn'],
      dtype='object')


In [ ]:
# Counting unique values
n = len(pd.unique(sampled_geohash_data_original['neighborhood']))
print("No.of.unique name values :", n)

No.of.unique name values : 215


In [ ]:
# Sampling by Geohash with Variable Sampling Fraction
sampled_geohash_data_base.shape

(518967, 30)

In [ ]:
# Sampling Entire Fractions of Grouped Data by Neighborhood
sampled_geohash_data_original.shape

(864936, 30)

### END SAMPLING

### Choropleth Maps
Choropleth maps are thematic maps where areas (such as regions, countries, or administrative boundaries) are shaded or patterned in proportion to the value of a variable being represented.

In [ ]:
# Sampled data scenario #2
# Sampling by Geohash with Variable Sampling Fraction

# Compute the frequency of occurrences of each unique value in the 'neighborhood' column of the 'sampled_geohash_data_base' DataFrame
shenzhen_taxi_pickup_sample2= sampled_geohash_data_base['neighborhood'].value_counts() # The result is stored in 'shenzhen_taxi_pickup_sample2'

# Reset the index of the 'shenzhen_taxi_pickup_sample2', converting the current index into a new column.
shenzhen_taxi_pickup_sample2 = shenzhen_taxi_pickup_sample2.reset_index()

# Rename the columns of the 'shenzhen_taxi_pickup_sample2' DataFrame to 'neighborhood' and 'count'
shenzhen_taxi_pickup_sample2.columns = ['neighborhood','count']

# Convert the 'neighborhood' column of the 'shenzhen_taxi_pickup_sample2' DataFrame to string type
shenzhen_taxi_pickup_sample2['neighborhood'] = shenzhen_taxi_pickup_sample2['neighborhood'].astype(str)

In [ ]:
# Original data

# Compute the frequency of occurrences of each unique value in the 'neighborhood' column of the 'sjoined_trips_original' DataFrame
shenzhen_taxi_pickup_original= sjoined_trips_original['neighborhood'].value_counts() # The result is stored in 'shenzhen_taxi_pickup_original'.

# Reset the index of the 'shenzhen_taxi_pickup_original' Series/DataFrame,  converting the current index into a new column.
shenzhen_taxi_pickup_original = shenzhen_taxi_pickup_original.reset_index()

# Rename the columns of the 'shenzhen_taxi_pickup_original' DataFrame to 'neighborhood' and 'count'.
shenzhen_taxi_pickup_original.columns = ['neighborhood','count']

# Convert the 'neighborhood' column of the 'shenzhen_taxi_pickup_original' DataFrame to string type.
shenzhen_taxi_pickup_original['neighborhood'] = shenzhen_taxi_pickup_original['neighborhood'].astype(str)

In [ ]:
# Display the first 6 rows of the Shenzhen_taxi_pickup_original
shenzhen_taxi_pickup_original.head(6)

neighborhood  count
0              Harlem  94500
1         East Harlem  84423
2        Williamsburg  70710
3             Astoria  44168
4            Elmhurst  34828
5  Bedford-Stuyvesant  33670

In [ ]:
# Create a choropleth map visualizing the distribution of taxi pickups across neighborhoods in Shenzhen - using original data

# Reference geo-map
shenzhen_taxi_pickup_original["neighborhood"].astype(str)

# Define the file path to the GeoJSON file containing neighborhood polygons
geo_path = r'/content/drive/MyDrive/Found. of DS Project/nyc_polygon.geojson'

# Define the scale for the heatmap based on specified threshold percentages
heatmap_scale = list()
threshold = [10,20,50,70,85,100]

for i in threshold :
    heatmap_scale.append(int(shenzhen_taxi_pickup_original['count'].max() * (i/100.0)))

# Initialize a Folium map centered on Shenzhen with a specified zoom level
map_shenzhen_taxi_pickup_sample = folium.Map(location=[40.730610, -73.935242], zoom_start=10)

# Create a choropleth layer on the Folium map using GeoJSON data and pickup count data
map_shenzhen_taxi_pickup_sample.choropleth(geo_data=geo_path, data=shenzhen_taxi_pickup_original, \
                data_out = 'nyc_zip_test.json',
             columns=['neighborhood', 'count'],
             #threshold_scale= heatmap_scale,
             key_on='feature.properties.neighborhood',
             fill_color='YlOrRd', fill_opacity=0.9, line_opacity=0.9,nan_fill_color='white',
             legend_name='Number of Pickups')

/usr/local/lib/python3.10/dist-packages/folium/folium.py:465: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  warnings.warn(


In [ ]:
# Display the choropleth map generated using Folium
map_shenzhen_taxi_pickup_sample

In [ ]:
# Create a choropleth map visualizing the distribution of taxi pickups across neighborhoods in Shenzhen - using sampled data (variable sampling fraction)

# Base geo-map (without Douglas Algorithm)

# Reference geo-map
shenzhen_taxi_pickup_sample2["neighborhood"].astype(str)

# Define the file path to the GeoJSON file containing neighborhood polygons
geo_path = r'/content/drive/MyDrive/Found. of DS Project/nyc_polygon.geojson'

# Define the scale for the heatmap based on specified threshold percentages
heatmap_scale = list()
threshold = [10,20,50,70,85,100]
for i in threshold :
    heatmap_scale.append(int(shenzhen_taxi_pickup_sample2['count'].max() * (i/100.0)))

# Initialize a Folium map centered on Shenzhen with a specified zoom level
map_shenzhen_taxi_pickup_sample = folium.Map(location=[40.730610, -73.935242], zoom_start=10)

# Create a choropleth layer on the Folium map using GeoJSON data and pickup count data
map_shenzhen_taxi_pickup_sample.choropleth(geo_data=geo_path, data=shenzhen_taxi_pickup_sample2, \
                data_out = 'nyc_zip_test.json',
             columns=['neighborhood', 'count'],
             #threshold_scale= heatmap_scale,
             key_on='feature.properties.neighborhood',
             fill_color='YlOrRd', fill_opacity=0.9, line_opacity=0.9,nan_fill_color='white',
             legend_name='Number of Pickups')

/usr/local/lib/python3.10/dist-packages/folium/folium.py:465: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  warnings.warn(


fill_color (string, optional) – Area fill color, defaults to blue. Can pass a hex code, color name, or if you are binding data, one of the following color brewer palettes: ‘BuGn’, ‘BuPu’, ‘GnBu’, ‘OrRd’, ‘PuBu’, ‘PuBuGn’, ‘PuRd’, ‘RdPu’, ‘YlGn’, ‘YlGnBu’, ‘YlOrBr’, and ‘YlOrRd’.

In [ ]:
# Display the choropleth map generated using Folium
map_shenzhen_taxi_pickup_sample

### END Choropleth Map generation

### Heatmap
A heatmap is a graphical representation of data in which values are depicted using a range of colors

### Heatmap (Longitude and Latitude Vs.	Count)
A heatmap is a graphical representation of data in which values are depicted using a range of colors

In [ ]:
# Import the HeatMap class from the folium.plugins module
from folium.plugins import HeatMap

In [ ]:
# Display the data types of each column in the DataFrame sjoined_trips_original
sjoined_trips_original.dtypes

id                          int64
VendorID                    int64
lpep_pickup_datetime       object
Lpep_dropoff_datetime      object
Store_and_fwd_flag         object
RateCodeID                  int64
longitude                 float64
latitude                  float64
Dropoff_longitude         float64
Dropoff_latitude          float64
Passenger_count             int64
Trip_distance             float64
Fare_amount               float64
Extra                     float64
MTA_tax                   float64
Tip_amount                float64
Tolls_amount              float64
Ehail_fee                 float64
improvement_surcharge     float64
Total_amount              float64
Payment_type                int64
Trip_type                 float64
geohash                    object
geometry                 geometry
index_right                 int64
neighborhood               object
boroughCode                object
borough                    object
@id                        object
geometryn     

In [ ]:
# Group the data by neighborhood, aggregating longitude and latitude values while counting the occurrences of each neighborhood
heatmap_data = sjoined_trips_original[['longitude','latitude','neighborhood']].groupby(['neighborhood'], as_index=False).agg({'longitude': 'first', 'latitude': 'first','neighborhood':'count'})


In [ ]:
# Rename the 'neighborhood' column to 'count' in the DataFrame heatmap_data
heatmap_data.rename(columns={'neighborhood': 'count'}, inplace=True)

In [ ]:
# Sort the DataFrame heatmap_data by the 'count' column in descending order
new_heatmap_data = heatmap_data.sort_values(by='count', ascending=False) # The result is stored in new_heatmap_data

In [ ]:
# Display the first two rows of the new_heatmap_data
new_heatmap_data.head(2)

longitude   latitude  count
98 -73.949448  40.812660  94500
62 -73.940697  40.793137  84423

In [ ]:
# Convert the DataFrame new_heatmap_data to a list
heatmap_data1 = new_heatmap_data.values.tolist()

In [ ]:
# Display the data types of columns in the DataFrame trips
trips.dtypes

id                         int64
VendorID                   int64
lpep_pickup_datetime      object
Lpep_dropoff_datetime     object
Store_and_fwd_flag        object
RateCodeID                 int64
longitude                float64
latitude                 float64
Dropoff_longitude        float64
Dropoff_latitude         float64
Passenger_count            int64
Trip_distance            float64
Fare_amount              float64
Extra                    float64
MTA_tax                  float64
Tip_amount               float64
Tolls_amount             float64
Ehail_fee                float64
improvement_surcharge    float64
Total_amount             float64
Payment_type               int64
Trip_type                float64
geohash                   object
count                      int64
dtype: object

In [ ]:
# Assigning a value of 1 to a new column 'count' in the DataFrame trips - 1 is added to each row in the column
trips['count'] = 1

In [ ]:
# Randomly sample 10,000 rows from the 'trips' DataFrame, selecting only the columns 'latitude', 'longitude', and 'count' for each sampled row
trips[['latitude', 'longitude', 'count']].sample(n=10000)

latitude  longitude  count
314472   40.804821 -73.961983      1
1184282  40.702969 -73.990501      1
507720   40.809086 -73.952972      1
652322   40.795227 -73.933128      1
26892    40.726719 -73.952469      1
...            ...        ...    ...
1196699  40.827663 -73.904419      1
150333   40.803799 -73.930801      1
1350554  40.815311 -73.954910      1
369640   40.799316 -73.936172      1
1298188  40.689865 -73.979362      1

[10000 rows x 3 columns]

In [ ]:
# Calculate the length of the list obtained after grouping the sampled trips DataFrame by latitude and longitude, summing up the counts, and converting it to a list of values
len(trips[['latitude', 'longitude', 'count']].sample(n=10000).groupby(['latitude', 'longitude']).sum().reset_index().values.tolist())

9981

In [ ]:
# Define a function to generate a base map using Folium with default location and zoom level
def generateBaseMap(default_location=[40.7306, -73.935], default_zoom_start=11):

    # Create a Folium map with the specified default location and zoom level
    base_map = folium.Map(location=default_location, control_scale=True, zoom_start=default_zoom_start)

    # Return the generated base map
    return base_map


In [ ]:
# Generate a base map using the generateBaseMap function
base_map = generateBaseMap()

# Create a HeatMap layer using the sampled data and add it to the base map
HeatMap(data=trips[['latitude', 'longitude', 'count']].sample(n=10000).groupby(['latitude', 'longitude']).sum().reset_index().values.tolist(),
        radius=8, max_zoom=13).add_to(base_map)

In [ ]:
# Display the base map with the HeatMap layer
base_map

In [ ]:
# Add a click-for-marker functionality to the base map
base_map.add_child(folium.ClickForMarker(popup='Potential Location'))


### Heatmap (Longitude and	Latitude Vs. Total Amount)

In [ ]:
# Select a random sample of 10,000 rows from the 'trips' DataFrame including only 'latitude', 'longitude', and 'Total_amount' in the sample
trips[['latitude', 'longitude', 'Total_amount']].sample(n=10000)

latitude  longitude  Total_amount
949834   40.714676 -73.944366         35.38
866106   40.801769 -73.949150         17.30
124541   40.680275 -73.945122          7.80
1375171  40.666092 -73.982246         12.36
493102   40.695671 -73.997467         28.20
...            ...        ...           ...
834802   40.686886 -73.990349         15.30
89695    40.721401 -73.844322         19.80
1413904  40.726749 -73.838966         30.80
961671   40.787857 -73.953835          6.80
309938   40.713551 -73.830276         12.88

[10000 rows x 3 columns]

In [ ]:
# Calculate the length of the list obtained by grouping the sampled data by latitude and longitude, summing the 'Total_amount' for each group, resetting the index, and converting to a list of values
len(trips[['latitude', 'longitude', 'Total_amount']].sample(n=10000).groupby(['latitude', 'longitude']).sum().reset_index().values.tolist())

9979

In [ ]:
# Displaying heatmap of longitute and latitude vs total amount
base_map2 = generateBaseMap()
HeatMap(data=trips[['latitude', 'longitude', 'Total_amount']].sample(n=10000).groupby(['latitude', 'longitude']).sum().reset_index().values.tolist(), radius=8, max_zoom=13).add_to(base_map2)
base_map2


In [ ]:
# Add a click-for-marker functionality to the base map
base_map2.add_child(folium.ClickForMarker(popup='Potential Location'))

### Heatmap (Longitude and	Latitude Vs. Trip Distance)

In [ ]:
# Sample 10,000 rows from the DataFrame 'trips', selecting the columns 'latitude', 'longitude', and 'Trip_distance'
trips[['latitude', 'longitude', 'Trip_distance']].sample(n=10000)

latitude  longitude  Trip_distance
965936   40.686417 -73.983498           0.90
1316694  40.732792 -73.863792           4.35
1190040  40.721390 -73.844292           0.40
436602   40.806770 -73.964661           1.38
688559   40.825195 -73.916534           9.37
...            ...        ...            ...
1219540  40.721363 -73.844292           9.29
1170738  40.807892 -73.945450           1.86
360128   40.718472 -73.959229           2.30
723318   40.766510 -73.921326           5.40
1025876  40.793915 -73.949242           1.02

[10000 rows x 3 columns]

In [ ]:
# Count the number of unique latitude and longitude pairs after sampling 10,000 rows from the DataFrame 'trips' and grouping by latitude and longitude, considering the 'Trip_distance' column.
len(trips[['latitude', 'longitude', 'Trip_distance']].sample(n=10000).groupby(['latitude', 'longitude']).sum().reset_index().values.tolist())

9983

In [ ]:
# Displaying heat map of longitute and latitude vs trip distance
base_map3 = generateBaseMap()
HeatMap(data=trips[['latitude', 'longitude', 'Trip_distance']].sample(n=10000).groupby(['latitude', 'longitude']).sum().reset_index().values.tolist(), radius=8, max_zoom=13).add_to(base_map3)
base_map3

### Heatmap (Longitude and Latitude Vs. Tolls_amount)

In [ ]:
# Sample 10,000 rows from the 'trips' DataFrame, selecting the 'latitude', 'longitude', and 'Tolls_amount' columns.
trips[['latitude', 'longitude', 'Tolls_amount']].sample(n=10000)

latitude  longitude  Tolls_amount
519678   40.671879 -73.984085           0.0
498470   40.713676 -73.829826           0.0
1300803  40.682301 -73.980804           0.0
241271   40.685799 -73.915871           0.0
965798   40.585632 -73.966209           0.0
...            ...        ...           ...
777153   40.836430 -73.943031           0.0
370144   40.684418 -73.989189           0.0
980791   40.814060 -73.940529           0.0
893717   40.683681 -73.976189           0.0
618188   40.811241 -73.959335           0.0

[10000 rows x 3 columns]

In [ ]:
# This code calculates the number of unique latitude-longitude combinations after sampling 10,000 rows from the 'trips' DataFrame and grouping them by latitude and longitude while summing the 'Tolls_amount' for each group.
len(trips[['latitude', 'longitude', 'Tolls_amount']].sample(n=10000).groupby(['latitude', 'longitude']).sum().reset_index().values.tolist())

9977

In [ ]:
# Displaying heat map of longitute and latitude vs tolls amount
base_map4 = generateBaseMap()
HeatMap(data=trips[['latitude', 'longitude', 'Tolls_amount']].sample(n=10000).groupby(['latitude', 'longitude']).sum().reset_index().values.tolist(), radius=8, max_zoom=13).add_to(base_map4)
base_map4

# Loading Data & Analysis: Air Quality Data

In [ ]:
# Read the CSV file into a pandas DataFrame named "trips"
air_quality = pd.read_csv("/content/drive/MyDrive/Found. of DS Project/NYC_air_quality.csv")

In [ ]:
# Return the type of the dataframe air_quality
type(air_quality)

pandas.core.frame.DataFrame

In [ ]:
# Retrive the number of rows and number of columns in the dataframe air_quality
air_quality.shape

(169999, 31)

In [ ]:
# Retrieve the first 2 rows of the DataFrame air_quality to inspect its structure and content
air_quality.head(2)

SensorID        time   latitude  longitude  bin0  bin1  bin2  bin3  \
0  NYCP2_CS01A  1631277304  40.847672 -73.869316    11     1     1     0   
1  NYCP2_CS01A  1631277308  40.847668 -73.869316    22     4     1     0   

   bin4  bin5  ...  bin17  bin18  bin19  bin20  bin21  bin22  bin23  \
0     0     0  ...      0      0      0      0      0      0      0   
1     0     2  ...      0      0      0      0      0      0      0   

   temperature  humidity      pm25  
0         23.7      57.3  4.508813  
1         23.7      57.8  5.462420  

[2 rows x 31 columns]

In [ ]:
# Retrieve the number of columns in the DataFrame air_quality
columns=air_quality.shape[1]
print(columns)

# Retrieve the number of rows in the DataFrame air_quality
rows_air_quality=air_quality.shape[0]
print(rows_air_quality)

31
169999


# Remove erroneous coordinates (0,0) from the dataset - Air Quality Data

In [ ]:
# Rename the 'Pickup_longitude' column to 'longitude'
# Rename 'Pickup_latitude' column to 'latitude' in the DataFrame air_quality
# The 'inplace=True' parameter ensures that the changes are applied to the DataFrame itself
air_quality.rename(columns={'Pickup_longitude':'longitude', 'Pickup_latitude':'latitude'}, inplace=True)

In [ ]:
# Filter the DataFrame air_quality to remove rows where the latitude is 0 and longitude is 0
air_quality = air_quality[(air_quality['latitude'] != 0 ) & (air_quality['longitude']!=0 )]

### Check the size before and after the filter

In [ ]:
#Before the filter
print("Before filtering:", rows_air_quality)

#After the filter
rows_air_quality2=air_quality.shape[0]
print("After filtering: ", rows_air_quality2)

Before filtering: 169999
After filtering:  169999


# Geohash - Air Quality Data

### Generate geohash for each tuple (long, lat)

In [ ]:
# Measure the execution time of the code within this cell
%%time

geohash_precision = 6

# Encode latitude and longitude coordinates into geohashes and assign them to a new column 'geohash' in the DataFrame air_quality
# The lambda function applies the encoding operation to each row of the DataFrame using the specified geohash precision
air_quality['geohash'] = air_quality.apply(lambda x: gh.encode(x.latitude, x.longitude, precision=geohash_precision), axis=1)


CPU times: user 4.92 s, sys: 85.9 ms, total: 5.01 s
Wall time: 5.02 s


In [ ]:
# Measure the average execution time of the trips.head(2) operation
%timeit air_quality.head(2)

24.1 µs ± 6.07 µs per loop (mean ± std. dev. of 7 runs, 10000 loops each)


In [ ]:
# Display number of rows
air_quality.shape[0]

169999

In [ ]:
# Display the first 2 rows
air_quality.head(2)

SensorID        time   latitude  longitude  bin0  bin1  bin2  bin3  \
0  NYCP2_CS01A  1631277304  40.847672 -73.869316    11     1     1     0   
1  NYCP2_CS01A  1631277308  40.847668 -73.869316    22     4     1     0   

   bin4  bin5  ...  bin18  bin19  bin20  bin21  bin22  bin23  temperature  \
0     0     0  ...      0      0      0      0      0      0         23.7   
1     0     2  ...      0      0      0      0      0      0         23.7   

   humidity      pm25  geohash  
0      57.3  4.508813   dr72rh  
1      57.8  5.462420   dr72rh  

[2 rows x 32 columns]

### Convert air_quality to GeoPandas

In [ ]:
# Return the type of dataframe air_quality
type(air_quality)

pandas.core.frame.DataFrame

In [ ]:
# Convert to Geopandas Geodataframe
%%time

# Create a GeoDataFrame gdf_air_quality from the DataFrame air_quality, specifying the geometry column using longitude and latitude coordinates
gdf_air_quality = gpd.GeoDataFrame(air_quality, geometry=gpd.points_from_xy(air_quality.longitude, air_quality.latitude))

CPU times: user 111 ms, sys: 20 ms, total: 131 ms
Wall time: 129 ms


In [ ]:
# Determine the type of object represented by the variable gdf_air_quality
type(gdf_air_quality)

geopandas.geodataframe.GeoDataFrame

In [ ]:
# Print the Coordinates Reference System (CRS) of the GeoDataFrame gdf_air_quality
print(gdf_air_quality.crs)

None


In [ ]:
# The CRS for trips should remain geographic 4326
gdf_air_quality = gdf_air_quality.set_crs('epsg:4326')
print(gdf_air_quality)

           SensorID        time   latitude  longitude  bin0  bin1  bin2  bin3  \
0       NYCP2_CS01A  1631277304  40.847672 -73.869316    11     1     1     0   
1       NYCP2_CS01A  1631277308  40.847668 -73.869316    22     4     1     0   
2       NYCP2_CS01A  1631277313  40.847649 -73.869362    40     1     1     0   
3       NYCP2_CS01A  1631277318  40.847649 -73.869362    26     1     0     0   
4       NYCP2_CS01A  1631277323  40.847649 -73.869362    44     4     0     1   
...             ...         ...        ...        ...   ...   ...   ...   ...   
169994  NYCP2_CS03A  1631457109  40.823353 -73.890488   115    11     2     0   
169995  NYCP2_CS03A  1631457114  40.823349 -73.890480   132     8     2     0   
169996  NYCP2_CS03A  1631457119  40.823349 -73.890480   147    14     0     0   
169997  NYCP2_CS03A  1631457124  40.823345 -73.890488   121     8     2     0   
169998  NYCP2_CS03A  1631457129  40.823338 -73.890488   135     8     1     0   

        bin4  bin5  ...  bi

In [ ]:
# Display the shape of the GeoDataFrame gdf_air_quality
gdf_air_quality.shape

(169999, 33)

In [ ]:
# Display the first 2 row of the GeoDataFrame gdf_air_quality
gdf_air_quality.head(2)

SensorID        time   latitude  longitude  bin0  bin1  bin2  bin3  \
0  NYCP2_CS01A  1631277304  40.847672 -73.869316    11     1     1     0   
1  NYCP2_CS01A  1631277308  40.847668 -73.869316    22     4     1     0   

   bin4  bin5  ...  bin19  bin20  bin21  bin22  bin23  temperature  humidity  \
0     0     0  ...      0      0      0      0      0         23.7      57.3   
1     0     2  ...      0      0      0      0      0         23.7      57.8   

       pm25  geohash                    geometry  
0  4.508813   dr72rh  POINT (-73.86932 40.84767)  
1  5.462420   dr72rh  POINT (-73.86932 40.84767)  

[2 rows x 33 columns]

it additionally air_quality now has geometry column

### Spatial Analysis and Join Operations with GeoDataFrames
Keeping geometry column from both dataframes when applying sjoin() using GeoPandas
this is so because later on we group by NAME(district in Shenzhen)
also, the CRS (coordinate reference system) is 3857 in this case which is a projected CRS not geographic CRS, to calculate the distance corercctly between centroids
https://gis.stackexchange.com/questions/393387/keeping-geometry-column-from-both-dataframes-when-applying-sjoin-using-geopand

In [ ]:
# Convert the geometry column to EPSG:3857 CRS for accurate spatial analysis.
neighborhoods_original['geometryn'] = neighborhoods_original.geometry.to_crs("epsg:3857")

# Retrieve the coordinate reference system (CRS) information from the GeoDataFrame gdf_air_quality
gdf_air_quality.crs

<Geographic 2D CRS: EPSG:4326>
Name: WGS 84
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
Area of Use:
- name: World.
- bounds: (-180.0, -90.0, 180.0, 90.0)
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [ ]:
%%time
# Perform a spatial join between gdf_trips and neighborhoods_original, considering trips that are within neighborhood polygons.

#BASELINE
# we join by sjoin, but we have geohash so, we sample stratified by geohash
# so, we join only to get the metrics but the stratified sampling is based on the fine-grained division (geohash in this case)

# Store the result of the spatial join in the variable sjoined_trips_original.
sjoined_air_quality_original = gpd.sjoin(gdf_air_quality, neighborhoods_original, predicate="within")

CPU times: user 691 ms, sys: 166 ms, total: 857 ms
Wall time: 857 ms


In [ ]:
sjoined_air_quality_original.head(2)

SensorID        time   latitude  longitude  bin0  bin1  bin2  bin3  \
0  NYCP2_CS01A  1631277304  40.847672 -73.869316    11     1     1     0   
1  NYCP2_CS01A  1631277308  40.847668 -73.869316    22     4     1     0   

   bin4  bin5  ...  humidity      pm25  geohash                    geometry  \
0     0     0  ...      57.3  4.508813   dr72rh  POINT (-73.86932 40.84767)   
1     0     2  ...      57.8  5.462420   dr72rh  POINT (-73.86932 40.84767)   

   index_right  neighborhood  boroughCode  borough  \
0           38    Bronx Park            2    Bronx   
1           38    Bronx Park            2    Bronx   

                                                 @id  \
0  http://nyc.pediacities.com/Resource/Neighborho...   
1  http://nyc.pediacities.com/Resource/Neighborho...   

                                           geometryn  
0  POLYGON ((-8223164.965 4991107.997, -8223015.9...  
1  POLYGON ((-8223164.965 4991107.997, -8223015.9...  

[2 rows x 39 columns]

In [ ]:
type(sjoined_air_quality_original)

geopandas.geodataframe.GeoDataFrame

In [ ]:
# Counting unique values
n = len(pd.unique(sjoined_air_quality_original['neighborhood']))
print("No.of.unique name values :", n)

No.of.unique name values : 48


In [ ]:
# Retrieve the shape of the sjoined_trips_original GeoDataFrame, which indicates the number of rows and columns in the dataset.
sjoined_air_quality_original.shape

(169995, 39)

In [ ]:
# Retrieve the data types of columns in the sjoined_trips_original GeoDataFrame, indicating the data type of each attribute or column.
sjoined_air_quality_original.dtypes

SensorID          object
time               int64
latitude         float64
longitude        float64
bin0               int64
bin1               int64
bin2               int64
bin3               int64
bin4               int64
bin5               int64
bin6               int64
bin7               int64
bin8               int64
bin9               int64
bin10              int64
bin11              int64
bin12              int64
bin13              int64
bin14              int64
bin15              int64
bin16              int64
bin17              int64
bin18              int64
bin19              int64
bin20              int64
bin21              int64
bin22              int64
bin23              int64
temperature      float64
humidity         float64
pm25             float64
geohash           object
geometry        geometry
index_right        int64
neighborhood      object
boroughCode       object
borough           object
@id               object
geometryn       geometry
dtype: object

# SAMPLING AND MAP GENERATION

##Sampling by Geohash with Variable Sampling Fraction

In [ ]:
%%time
# Sampling by geohash change fraction sampling rate
# Group the spatially joined data 'sjoined_air_quality_original' by neighborhood
# Then within each neighborhood group, sample a fraction of the data based on the specified 'sampling_fraction'.

sampled_geohash_data_base_airquality= sjoined_air_quality_original.groupby('neighborhood').apply(lambda x: x.sample(frac=sampling_fraction)) #sampling_fraction = 0.6
# The resulting sampled data is stored in the 'sampled_geohash_data_base' variable.

CPU times: user 497 ms, sys: 29.8 ms, total: 527 ms
Wall time: 530 ms


In [ ]:
# Retrieve the shape of the sampled_geohash_data_base DataFrame, indicating the number of rows and columns in the dataset.
sampled_geohash_data_base_airquality.shape

(101999, 39)

In [ ]:
# Print the first two rows
sampled_geohash_data_base_airquality.head(2)

SensorID        time   latitude  longitude  bin0  bin1  \
neighborhood                                                                    
Allerton     95442  NYCP2_CS01A  1636274849  40.858307 -73.867912   201     0   
             95461  NYCP2_CS01A  1636274944  40.862850 -73.866028    90     1   

                    bin2  bin3  bin4  bin5  ...  humidity      pm25  geohash  \
neighborhood                                ...                                
Allerton     95442     0     1     0     1  ...      87.0  4.813178   dr72rn   
             95461     0     0     0     0  ...      84.4  3.019981   dr72rn   

                                      geometry  index_right  neighborhood  \
neighborhood                                                                
Allerton     95442  POINT (-73.86791 40.85831)            0      Allerton   
             95461  POINT (-73.86603 40.86285)            0      Allerton   

                    boroughCode  borough  \
neighborhood                               
Allerton     95442            2    Bronx   
             95461            2    Bronx   

                                                                  @id  \
neighborhood                                                            
Allerton     95442  http://nyc.pediacities.com/Resource/Neighborho...   
             95461  http://nyc.pediacities.com/Resource/Neighborho...   

                                                            geometryn  
neighborhood                                                           
Allerton     95442  POLYGON ((-8220788.214 4993431.406, -8220479.3...  
             95461  POLYGON ((-8220788.214 4993431.406, -8220479.3...  

[2 rows x 39 columns]

In [ ]:
# Print the column names of the sampled_geohash_data_base DataFrame, showing the attributes present in the dataset.
print(sampled_geohash_data_base_airquality.columns)

Index(['SensorID', 'time', 'latitude', 'longitude', 'bin0', 'bin1', 'bin2',
       'bin3', 'bin4', 'bin5', 'bin6', 'bin7', 'bin8', 'bin9', 'bin10',
       'bin11', 'bin12', 'bin13', 'bin14', 'bin15', 'bin16', 'bin17', 'bin18',
       'bin19', 'bin20', 'bin21', 'bin22', 'bin23', 'temperature', 'humidity',
       'pm25', 'geohash', 'geometry', 'index_right', 'neighborhood',
       'boroughCode', 'borough', '@id', 'geometryn'],
      dtype='object')


In [ ]:
# counting unique values
n = len(pd.unique(sampled_geohash_data_base_airquality['neighborhood']))
print("No.of.unique name values :", n)

No.of.unique name values : 48


## Sampling Entire Fractions of Grouped Data by Neighborhood

In [ ]:
%%time
# Original

# Group the spatially joined data 'sjoined_trips_original' by neighborhood, then within each neighborhood group, sample the entire fraction of the data (frac=1).
sampled_geohash_data_original_airquality = sjoined_air_quality_original.groupby('neighborhood').apply(lambda x: x.sample(frac=1))
# The resulting sampled data is stored in the 'sampled_geohash_data_original' variable

CPU times: user 668 ms, sys: 27.7 ms, total: 696 ms
Wall time: 727 ms


In [ ]:
# Retrieve the shape of the sampled_geohash_data_base DataFrame, indicating the number of rows and columns in the dataset.
sampled_geohash_data_original_airquality.shape

(169995, 39)

In [ ]:
# Print the first two rows
sampled_geohash_data_original_airquality.head(2)

SensorID        time   latitude  longitude  bin0  bin1  \
neighborhood                                                                    
Allerton     95495  NYCP2_CS01A  1636275114  40.862938 -73.866028   100     5   
             95524  NYCP2_CS01A  1636275259  40.862976 -73.866005    98     1   

                    bin2  bin3  bin4  bin5  ...  humidity      pm25  geohash  \
neighborhood                                ...                                
Allerton     95495     0     0     0     0  ...      83.4  2.713955   dr72rn   
             95524     0     0     0     0  ...      82.1  2.713955   dr72rn   

                                      geometry  index_right  neighborhood  \
neighborhood                                                                
Allerton     95495  POINT (-73.86603 40.86294)            0      Allerton   
             95524  POINT (-73.86601 40.86298)            0      Allerton   

                    boroughCode  borough  \
neighborhood                               
Allerton     95495            2    Bronx   
             95524            2    Bronx   

                                                                  @id  \
neighborhood                                                            
Allerton     95495  http://nyc.pediacities.com/Resource/Neighborho...   
             95524  http://nyc.pediacities.com/Resource/Neighborho...   

                                                            geometryn  
neighborhood                                                           
Allerton     95495  POLYGON ((-8220788.214 4993431.406, -8220479.3...  
             95524  POLYGON ((-8220788.214 4993431.406, -8220479.3...  

[2 rows x 39 columns]

In [ ]:
# Print the column names of the sampled_geohash_data_original DataFrame, showing the attributes present in the dataset.
print(sampled_geohash_data_original_airquality.columns)

Index(['SensorID', 'time', 'latitude', 'longitude', 'bin0', 'bin1', 'bin2',
       'bin3', 'bin4', 'bin5', 'bin6', 'bin7', 'bin8', 'bin9', 'bin10',
       'bin11', 'bin12', 'bin13', 'bin14', 'bin15', 'bin16', 'bin17', 'bin18',
       'bin19', 'bin20', 'bin21', 'bin22', 'bin23', 'temperature', 'humidity',
       'pm25', 'geohash', 'geometry', 'index_right', 'neighborhood',
       'boroughCode', 'borough', '@id', 'geometryn'],
      dtype='object')


In [ ]:
# Counting unique values
n = len(pd.unique(sampled_geohash_data_original_airquality['neighborhood']))
print("No.of.unique name values :", n)

No.of.unique name values : 48


In [ ]:
# Sampling by Geohash with Variable Sampling Fraction
sampled_geohash_data_base_airquality.shape

(101999, 39)

## Choropleth Maps
Choropleth maps are thematic maps where areas (such as regions, countries, or administrative boundaries) are shaded or patterned in proportion to the value of a variable being represented.

In [ ]:
import geopandas as gpd
import folium

# Define the file path to the GeoJSON file containing neighborhood polygons
geojson_file = "/content/drive/MyDrive/Found. of DS Project/nyc_polygon.geojson"

# Read the GeoJSON file and create a GeoDataFrame named neighborhoods_original
neighborhoods_original = gpd.read_file(geojson_file)

# Perform a spatial join between gdf_air_quality and neighborhoods_original, considering locations that are within neighborhood polygons
sjoined_air_quality = gpd.sjoin(gdf_air_quality, neighborhoods_original, how="inner", op="within")

# Count the number of air quality readings in each neighborhood
neighborhood_counts = sjoined_air_quality['neighborhood'].value_counts().reset_index()
neighborhood_counts.columns = ['neighborhood', 'count']



/usr/local/lib/python3.10/dist-packages/IPython/core/interactiveshell.py:3473: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  if (await self.run_code(code, result,  async_=asy)):


In [ ]:
# Initialize a Folium map centered on New York City with a specified zoom level
map_air_quality = folium.Map(location=[40.730610, -73.935242], zoom_start=10)

# Create a choropleth layer on the Folium map using GeoJSON data and air quality metrics
# choropleth map showing air quality metrics (e.g., count of readings) across different
# neighborhoods in New York City
map_air_quality.choropleth(
    geo_data=geojson_file,  # GeoJSON file containing neighborhood polygons
    data=neighborhood_counts,  # Air quality metrics data
    columns=['neighborhood', 'count'],  # Columns specifying neighborhood ID and metric values
    key_on='feature.properties.neighborhood',  # Key to join neighborhood IDs in GeoJSON data and air quality metrics
    fill_color='YlOrRd',  # Color scale for choropleth map
    fill_opacity=0.4,  # Opacity of filled areas
    line_opacity=0.9,  # Opacity of boundary lines
    legend_name='Air Quality Metrics'  # Title for the legend
)

# Display the choropleth map
map_air_quality


/usr/local/lib/python3.10/dist-packages/folium/folium.py:465: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  warnings.warn(


## Heatmap
A heatmap is a graphical representation of data in which values are depicted using a range of colors

In [ ]:
# Import the HeatMap class from the folium.plugins module
from folium.plugins import HeatMap
# Display the data types of each column in the DataFrame sjoined_trips_original
sjoined_air_quality_original.dtypes

SensorID          object
time               int64
latitude         float64
longitude        float64
bin0               int64
bin1               int64
bin2               int64
bin3               int64
bin4               int64
bin5               int64
bin6               int64
bin7               int64
bin8               int64
bin9               int64
bin10              int64
bin11              int64
bin12              int64
bin13              int64
bin14              int64
bin15              int64
bin16              int64
bin17              int64
bin18              int64
bin19              int64
bin20              int64
bin21              int64
bin22              int64
bin23              int64
temperature      float64
humidity         float64
pm25             float64
geohash           object
geometry        geometry
index_right        int64
neighborhood      object
boroughCode       object
borough           object
@id               object
geometryn       geometry
dtype: object

In [ ]:
# Define a function to generate a base map using Folium with default location and zoom level
def generateBaseMap(default_location=[40.7306, -73.935], default_zoom_start=11):

    # Create a Folium map with the specified default location and zoom level
    base_map= folium.Map(location=default_location, control_scale=True, zoom_start=default_zoom_start)

    # Return the generated base map
    return base_map

### HeatMap (Longitude and Latituse VS. Temperature)

In [ ]:
# Select a random sample of 10,000 rows from the 'trips' DataFrame including only 'latitude', 'longitude', and 'Total_amount' in the sample
air_quality[['latitude', 'longitude', 'temperature']].sample(n=10000)

latitude  longitude  temperature
154826  40.821262 -73.886467         15.0
167584  40.818867 -73.898369         29.7
31899   40.811226 -73.914742         19.8
14710   40.813587 -73.913261         17.9
134162  40.845562 -73.870613          7.3
...           ...        ...          ...
66386   40.844532 -73.871162         18.3
8395    40.846558 -73.870018         15.7
154199  40.829952 -73.891792         17.7
24313   40.846802 -73.870026         20.9
160826  40.813152 -73.889748         21.4

[10000 rows x 3 columns]

In [ ]:
# Calculate the length of the list obtained by grouping the sampled data by latitude and longitude, summing the 'Total_amount' for each group, resetting the index, and converting to a list of values
len(air_quality[['latitude', 'longitude', 'temperature']].sample(n=10000).groupby(['latitude', 'longitude']).sum().reset_index().values.tolist())

9001

In [ ]:
# Generate a base map using the generateBaseMap function
base_map_aq_1 = generateBaseMap()

# Create a HeatMap layer using the sampled data and add it to the base map
HeatMap(data=air_quality[['latitude', 'longitude', 'temperature']].sample(n=10000).groupby(['latitude', 'longitude']).sum().reset_index().values.tolist(),
        radius=8, max_zoom=13).add_to(base_map_aq_1)
base_map_aq_1


# Combining Mobility and Air Data

### First Try (did not work)

In [ ]:
trips.head()
list(trips.columns)

['id',
 'VendorID',
 'lpep_pickup_datetime',
 'Lpep_dropoff_datetime',
 'Store_and_fwd_flag',
 'RateCodeID',
 'longitude',
 'latitude',
 'Dropoff_longitude',
 'Dropoff_latitude',
 'Passenger_count',
 'Trip_distance',
 'Fare_amount',
 'Extra',
 'MTA_tax',
 'Tip_amount',
 'Tolls_amount',
 'Ehail_fee',
 'improvement_surcharge',
 'Total_amount',
 'Payment_type',
 'Trip_type',
 'geohash',
 'count']

In [ ]:
gdf_trips['geohash']

1079814    dr5rkr
1274870    dr5rvg
1004918    dr5x83
1086616    dr5rs2
836743     dr5rk7
            ...  
1408926    dr5rv5
1201458    dr72j1
508023     dr5ry3
27449      dr5rv6
1168947    dr5rxt
Name: geohash, Length: 865666, dtype: object

In [ ]:
gdf_air_quality['geohash']

0         dr72rh
1         dr72rh
2         dr72rh
3         dr72rh
4         dr72rh
           ...  
169994    dr72nx
169995    dr72nx
169996    dr72nx
169997    dr72nx
169998    dr72nx
Name: geohash, Length: 169999, dtype: object

In [ ]:
air_quality.head()
list(air_quality.columns)

['SensorID',
 'time',
 'latitude',
 'longitude',
 'bin0',
 'bin1',
 'bin2',
 'bin3',
 'bin4',
 'bin5',
 'bin6',
 'bin7',
 'bin8',
 'bin9',
 'bin10',
 'bin11',
 'bin12',
 'bin13',
 'bin14',
 'bin15',
 'bin16',
 'bin17',
 'bin18',
 'bin19',
 'bin20',
 'bin21',
 'bin22',
 'bin23',
 'temperature',
 'humidity',
 'pm25',
 'geohash']

sjoined_combined contains the combined data from both datasets where the geohash values intersect, indicating that they are in the same or nearby locations.

In [ ]:
# Perform a spatial join between gdf_trips and gdf_air_quality using the geohash column
sjoined_combined = gpd.sjoin(gdf_trips, gdf_air_quality, how="inner", op="intersects", lsuffix="_trips", rsuffix="_air")

# Display the first 2 rows of the resulting GeoDataFrame.
sjoined_combined.head(2)


/usr/local/lib/python3.10/dist-packages/IPython/core/interactiveshell.py:3473: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  if (await self.run_code(code, result,  async_=asy)):


Empty GeoDataFrame
Columns: [id, VendorID, lpep_pickup_datetime, Lpep_dropoff_datetime, Store_and_fwd_flag, RateCodeID, longitude__trips, latitude__trips, Dropoff_longitude, Dropoff_latitude, Passenger_count, Trip_distance, Fare_amount, Extra, MTA_tax, Tip_amount, Tolls_amount, Ehail_fee, improvement_surcharge, Total_amount, Payment_type, Trip_type, geohash__trips, geometry, index__air, SensorID, time, latitude__air, longitude__air, bin0, bin1, bin2, bin3, bin4, bin5, bin6, bin7, bin8, bin9, bin10, bin11, bin12, bin13, bin14, bin15, bin16, bin17, bin18, bin19, bin20, bin21, bin22, bin23, temperature, humidity, pm25, geohash__air]
Index: []

[0 rows x 57 columns]

In [ ]:
# Print sample rows from gdf_trips and gdf_air_quality to check geohash values
print(gdf_trips.head())
print(gdf_air_quality.head())

# Check for common geohashes between the two datasets
common_geohashes = set(gdf_trips['geohash']).intersection(gdf_air_quality['geohash'])
print(common_geohashes)

# Adjust spatial join parameters if necessary
sjoined_combined = gpd.sjoin(gdf_trips, gdf_air_quality, how="inner", op="intersects")

# Check if sjoined_combined has any values after the spatial join
if not sjoined_combined.empty:
    print(sjoined_combined.head())
    # Proceed with further analysis and visualization
else:
    print("No matches found in the spatial join. Adjust parameters or check data compatibility.")


              id  VendorID lpep_pickup_datetime Lpep_dropoff_datetime  \
1079814  1079814         2  2016-01-24 18:32:26   2016-01-24 19:02:45   
1274870  1274870         1  2016-01-29 04:35:57   2016-01-29 04:45:36   
1004918  1004918         2  2016-01-22 06:01:51   2016-01-22 06:08:48   
1086616  1086616         1  2016-01-24 21:54:05   2016-01-24 21:58:53   
836743    836743         1  2016-01-18 11:05:48   2016-01-18 11:10:42   

        Store_and_fwd_flag  RateCodeID  longitude   latitude  \
1079814                  N           1 -73.992470  40.689507   
1274870                  N           1 -73.920799  40.756733   
1004918                  N           1 -73.807320  40.700222   
1086616                  N           1 -73.988937  40.693462   
836743                   N           1 -73.987556  40.669857   

         Dropoff_longitude  Dropoff_latitude  ...  MTA_tax  Tip_amount  \
1079814         -74.004578         40.751144  ...      0.5         0.0   
1274870         -73.877724  

/usr/local/lib/python3.10/dist-packages/IPython/core/interactiveshell.py:3473: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  if (await self.run_code(code, result,  async_=asy)):


No matches found in the spatial join. Adjust parameters or check data compatibility.


No common geohash's were found! we need to look for another way

In [ ]:
!pip install geohash2

ERROR: Operation cancelled by user


In [ ]:
!pip install geopy

ERROR: Operation cancelled by user


In [ ]:
import pandas as pd
import geohash2
from geopy.distance import geodesic

# Assuming 'trips' and 'air_quality' are your pandas DataFrames containing mobility and air quality data, respectively

# Define the precision level for geohash encoding
precision = 6

# Encode latitude and longitude coordinates to geohash for trips and air quality data
trips['geohash'] = trips.apply(lambda x: geohash2.encode(x.latitude, x.longitude, precision), axis=1)
air_quality['geohash'] = air_quality.apply(lambda x: geohash2.encode(x.latitude, x.longitude, precision), axis=1)

# Perform an inner merge based on geohash
merged_data = pd.merge(trips, air_quality, on='geohash', how='inner')

# Define the threshold for spatial relationship (e.g., 1000 meters)
threshold = 1000

# Function to check spatial relationship based on distance threshold
def spatial_relationship(row):
    mobility_coords = (row['latitude_x'], row['longitude_x'])
    air_quality_coords = (row['latitude_y'], row['longitude_y'])
    distance = geodesic(mobility_coords, air_quality_coords).meters  # Calculate distance in meters
    return distance <= threshold

# Apply spatial relationship check to the merged dataset
merged_data['is_related'] = merged_data.apply(spatial_relationship, axis=1)

# Filter the dataset to include only related data points
related_data = merged_data[merged_data['is_related']]

# Display the related data points
print(related_data.head())


KeyboardInterrupt: 

### Second Try

In [ ]:
!pip install geohash2
!pip install geopy


In [ ]:
from geopy.distance import geodesic

def spatial_relationship(mobility_point, air_quality_point, threshold=1000):

    mobility_coords = (mobility_point['latitude'], mobility_point['longitude'])
    air_quality_coords = (air_quality_point['latitude'], air_quality_point['longitude'])
    distance = geodesic(mobility_coords, air_quality_coords).meters  # Calculate distance in meters
    return distance <= threshold


In [ ]:
import geohash2

# Define the precision level for geohash encoding
precision = 6  # Adjust the precision level as needed


# Encode latitude and longitude coordinates to geohash
trips['geohash'] = trips.apply(lambda x: geohash2.encode(x.latitude, x.longitude, precision), axis=1)
air_quality['geohash'] = air_quality.apply(lambda x: geohash2.encode(x.latitude, x.longitude, precision), axis=1)

# Perform an inner merge based on GeoHash
combined_data = pd.merge(trips, air_quality, on='geohash', how='inner')

# Display the combined data
print(combined_data.head())

 #The code keeps crashing here because of insufficient RAM


In [ ]:
# Initial Filtering using Geohash
potential_matches = []
for geohash_prefix in trips['geohash'].str[:precision].unique():
    nearby_air_quality = air_quality[air_quality['geohash'].str.startswith(geohash_prefix)]
    if not nearby_air_quality.empty:
        potential_matches.append((geohash_prefix, nearby_air_quality))


matched_pairs = []
for geohash_prefix, nearby_air_quality in potential_matches:
    for _, mobility_point in trips[trips['geohash'].str.startswith(geohash_prefix)].iterrows():
        # Perform detailed spatial join or proximity check with nearby_air_quality
        if spatial_relationship(mobility_point, nearby_air_quality.iloc[0]):  # Passing the first nearby air quality point
            matched_pairs.append((mobility_point, nearby_air_quality))
            #print(f"Match found - Mobility Point: {mobility_point}, Air Quality Point: {nearby_air_quality.iloc[0]}")

# Output: matched_pairs contains the final matched pairs of mobility data and air quality data

We found matched geohash's, next step is to visualize

#Visualizing Combined Data (still working on it)

In [ ]:
import folium

# Initialize a Folium map
mymap = folium.Map(location=[40.7128, -74.0060], zoom_start=10)

# Add markers for matched points
for pair in matched_pairs:
    folium.Marker([pair[0]['latitude'], pair[0]['longitude']], popup=f"PM2.5: {pair[1]['pm25']}").add_to(mymap)

# Display the map
mymap.save('matched_points_map.html')
#mymap


In [ ]:
# Display the map using IFrame
from IPython.display import IFrame
IFrame(src='matched_points_map.html', width=700, height=600)

# Profiling the Datasets 28/03/2024

## Profiling the Mobility Dataset

In [8]:
# Load Mobility Dataset
mobility_df = pd.read_csv("/content/drive/MyDrive/Found. of DS Project/nyc_mobility/nyc1.csv")

# Profiling the Mobility Dataset
print("Mobility Dataset Profiling:")
print("=============================")
print("Data Types:")
print(mobility_df.dtypes)
print("\nSummary Statistics:")
print(mobility_df.describe())
print("\nMissing Values:")
print(mobility_df.isnull().sum())

# Visualizing the distribution of numerical data in Mobility Dataset
'''numerical_columns = mobility_df.select_dtypes(include=['float64', 'int64']).columns
for col in numerical_columns:
    plt.figure(figsize=(8, 6))
    sns.histplot(mobility_df[col], kde=True)
    plt.title(f'Distribution of {col}')
    plt.xlabel(col)
    plt.ylabel('Frequency')
    plt.show()'''

Mobility Dataset Profiling:
Data Types:
id                         int64
VendorID                   int64
lpep_pickup_datetime      object
Lpep_dropoff_datetime     object
Store_and_fwd_flag        object
RateCodeID                 int64
Pickup_longitude         float64
Pickup_latitude          float64
Dropoff_longitude        float64
Dropoff_latitude         float64
Passenger_count            int64
Trip_distance            float64
Fare_amount              float64
Extra                    float64
MTA_tax                  float64
Tip_amount               float64
Tolls_amount             float64
Ehail_fee                float64
improvement_surcharge    float64
Total_amount             float64
Payment_type               int64
Trip_type                float64
dtype: object

Summary Statistics:
                 id      VendorID    RateCodeID  Pickup_longitude  \
count  1.445285e+06  1.445285e+06  1.445285e+06      1.445285e+06   
mean   7.226420e+05  1.781941e+00  1.097067e+00     -7.381009

"numerical_columns = mobility_df.select_dtypes(include=['float64', 'int64']).columns\nfor col in numerical_columns:\n    plt.figure(figsize=(8, 6))\n    sns.histplot(mobility_df[col], kde=True)\n    plt.title(f'Distribution of {col}')\n    plt.xlabel(col)\n    plt.ylabel('Frequency')\n    plt.show()"

Insights:

(1) Data Types: Most of the columns appear to be numerical (int64 and float64), except for lpep_pickup_datetime, Lpep_dropoff_datetime, and Store_and_fwd_flag, which are objects (likely representing timestamps and flags).

(2) Summary Statistics:

Several columns have a wide range of values, as seen from the difference between the minimum and maximum values. For instance, Fare_amount, Trip_distance, and Total_amount have considerable variations.
Some columns, such as Passenger_count and Trip_type, seem to have discrete values, with a mean that doesn't necessarily provide a clear representation of the central tendency due to their discrete nature.

(3) Missing Values:

The Ehail_fee column seems to have no values at all, as indicated by all missing values (NaN). There are two missing values in the Trip_type column.

(4) Distribution of Numerical Columns:

From the histograms, you can see the distributions of various numerical columns. Some columns, like Fare_amount, Trip_distance, and Total_amount, appear to have right-skewed distributions, indicating that a majority of trips might have lower values while a few have significantly higher values.

In [9]:
# Drop the Ehail_fee column
mobility_df.drop(columns=['Ehail_fee'], inplace=True)

# Drop rows with missing values in the Trip_type column
mobility_df.dropna(subset=['Trip_type'], inplace=True)

## Profiling the Air Dataset

In [10]:
# Load Air Data Dataset
air_df = pd.read_csv("/content/drive/MyDrive/Found. of DS Project/NYC_air_quality.csv")

# Profiling the Air Data Dataset
print("\nAir Data Dataset Profiling:")
print("=============================")
print("Data Types:")
print(air_df.dtypes)
print("\nSummary Statistics:")
print(air_df.describe())
print("\nMissing Values:")
print(air_df.isnull().sum())

# Visualizing the distribution of numerical data in Air Data Dataset
'''numerical_columns_air = air_df.select_dtypes(include=['float64', 'int64']).columns
for col in numerical_columns_air:
    plt.figure(figsize=(8, 6))
    sns.histplot(air_df[col], kde=True)
    plt.title(f'Distribution of {col}')
    plt.xlabel(col)
    plt.ylabel('Frequency')
    plt.show()'''


Air Data Dataset Profiling:
Data Types:
SensorID        object
time             int64
latitude       float64
longitude      float64
bin0             int64
bin1             int64
bin2             int64
bin3             int64
bin4             int64
bin5             int64
bin6             int64
bin7             int64
bin8             int64
bin9             int64
bin10            int64
bin11            int64
bin12            int64
bin13            int64
bin14            int64
bin15            int64
bin16            int64
bin17            int64
bin18            int64
bin19            int64
bin20            int64
bin21            int64
bin22            int64
bin23            int64
temperature    float64
humidity       float64
pm25           float64
dtype: object

Summary Statistics:
               time       latitude      longitude           bin0  \
count  1.699990e+05  169999.000000  169999.000000  169999.000000   
mean   1.634506e+09      40.826202     -73.892555      78.485926   
std    

"numerical_columns_air = air_df.select_dtypes(include=['float64', 'int64']).columns\nfor col in numerical_columns_air:\n    plt.figure(figsize=(8, 6))\n    sns.histplot(air_df[col], kde=True)\n    plt.title(f'Distribution of {col}')\n    plt.xlabel(col)\n    plt.ylabel('Frequency')\n    plt.show()"

Insights:
(1) Data Types: Most columns are numerical (int64 and float64), representing various measurements such as sensor readings, geographical coordinates, temperature, humidity, and pm2.5 levels.

(2)Summary Statistics: The summary statistics provide insights into the distribution and characteristics of the numerical variables. For instance, the bin columns represent particle counts in different size bins, with varying means and standard deviations. The temperature, humidity, and pm25 columns also exhibit a range of values with different central tendencies and spreads.

(3) Missing Values: There are no missing values in any of the columns, which simplifies the data cleaning process.

(4) Distribution of Numerical Columns: The histograms visualize the distributions of the numerical columns, showing the spread and shape of each distribution.

# Exploring Relationships between Datasets 28/03/2024

## Common Attributes for Joining

We looked for common attributes between the datasets that can serve as keys for joining. These include timestamps, geographical coordinates, or other identifiers.
In the Mobility Dataset, we have timestamps for pickup and drop-off (lpep_pickup_datetime and Lpep_dropoff_datetime), as well as geographical coordinates (Pickup_longitude, Pickup_latitude, Dropoff_longitude, Dropoff_latitude).
In the Air Data Dataset, we have timestamps (time) and geographical coordinates (latitude, longitude).

In [11]:
# Print column names for the Mobility Dataset
print("Columns in Mobility Dataset:")
print("============================")
print(mobility_df.columns)

# Print column names for the Air Data Dataset
print("\nColumns in Air Data Dataset:")
print("=============================")
print(air_df.columns)

# Identify common attributes between the datasets
common_attributes = set(mobility_df.columns).intersection(set(air_df.columns))
print("\nCommon Attributes:")
print("===================")
print(common_attributes)


Columns in Mobility Dataset:
Index(['id', 'VendorID', 'lpep_pickup_datetime', 'Lpep_dropoff_datetime',
       'Store_and_fwd_flag', 'RateCodeID', 'Pickup_longitude',
       'Pickup_latitude', 'Dropoff_longitude', 'Dropoff_latitude',
       'Passenger_count', 'Trip_distance', 'Fare_amount', 'Extra', 'MTA_tax',
       'Tip_amount', 'Tolls_amount', 'improvement_surcharge', 'Total_amount',
       'Payment_type', 'Trip_type'],
      dtype='object')

Columns in Air Data Dataset:
Index(['SensorID', 'time', 'latitude', 'longitude', 'bin0', 'bin1', 'bin2',
       'bin3', 'bin4', 'bin5', 'bin6', 'bin7', 'bin8', 'bin9', 'bin10',
       'bin11', 'bin12', 'bin13', 'bin14', 'bin15', 'bin16', 'bin17', 'bin18',
       'bin19', 'bin20', 'bin21', 'bin22', 'bin23', 'temperature', 'humidity',
       'pm25'],
      dtype='object')

Common Attributes:
set()


Insights:  Both datasets indeed have longitude and latitude columns, which can be utilized for spatial analysis.

In [ ]:
from scipy.spatial.distance import cdist

# Extract latitude and longitude columns
mobility_coords = mobility_df[['Pickup_latitude', 'Pickup_longitude']].values
air_coords = air_df[['latitude', 'longitude']].values

# Calculate distances between each pair of mobility and air quality coordinates
distances = cdist(mobility_coords, air_coords, 'euclidean')

# Find the minimum distance for each mobility event
min_distances = distances.min(axis=1)

# Plot histogram of minimum distances
plt.hist(min_distances, bins=20, color='skyblue', edgecolor='black')
plt.xlabel('Distance (degrees)')
plt.ylabel('Frequency')
plt.title('Spatial Proximity Between Mobility Events and Air Quality Sensors')
plt.show()

## Temporal or Spatial Relationship

We checked if there's a temporal or spatial relationship between the datasets.

For example, you could examine if air quality data collected at certain timestamps or locations coincides with mobility data.
You can plot the data on a map to visualize the spatial distribution of mobility pickups/drop-offs and air quality sensor locations.
Analyze if there are patterns or trends in the data over time or across different locations.

## Correlation Analysis

Explore potential correlations between relevant columns in the datasets, such as trip distance, fare amount, passenger count, and air quality measurements (e.g., pm2.5 levels, temperature, humidity).
Calculate correlation coefficients (e.g., Pearson correlation) to quantify the strength and direction of relationships between variables.
Visualize correlations using scatter plots, heatmaps, or other graphical representations.

# Proposing a Simple Manual Algorithmic Solution for the Join Operation
Identify Key Attributes: Determine the common attribute(s) on which you want to perform the join (e.g., location, time).
Nested Loop Join Algorithm:
Iterate through each record in the Mobility Dataset.
For each record, search for matching records in the Air Data Dataset based on the key attribute(s).
If a match is found, combine the records from both datasets into a single record.
Repeat this process until all records in the Mobility Dataset are processed.
Performance Consideration: Depending on the size of the datasets, you may need to consider optimizations such as indexing or parallel processing to improve performance.

# Evaluation and Validation
Evaluate Results: Assess the effectiveness and efficiency of the proposed join algorithm.
Validation: Validate the joined dataset to ensure correctness and completeness.